In [108]:
#import libraries
import os
import pandas as pd 
import numpy as np 
import matplotlib as plt
import seaborn as sns 
import gdown
from collections import defaultdict
import requests
from bs4 import BeautifulSoup

# Functions

#### fixing '5E54' becoming '5.00E+54' issue

In [109]:
def fix_PDB_ID(df):
    for i, j in enumerate(df['PDB_ID']):
        print (j)
        if len(str(j))>4:
            if '-' in j:
                X= ''.join(j.split('-')).upper()
                df.loc[i, 'PDB_ID']= X
            else:
                if '.' in j:
                    x= str(j)
                    x1= x.split('.')[0]
                    x2= x.split('+')[1]
                    X= x1+'E'+x2
                    print (X)
                    df.loc[i, 'PDB_ID']= X
                else:
                    x= str(j)
                    x1= x.split('+')[0]
                    x2= x.split('+')[1]
                    X= x1+ x2
                    print (X)
                    df.loc[i, 'PDB_ID']= X
                    
    return (df)

#### Function to identify base pair of interest

In [110]:
def find_bp_interest(df, bp, hbonds):
    if bp.split('-')[0] != bp.split('-')[1]:
        bps= [bp, "-".join(bp.split("-")[::-1])]
    else:
        bps= [bp]
        
    df1= df[df['base_pair'].isin(bps)]
    df1.index= np.arange(0, len(df1))
    
    def extract_bp(row, hbond):
        hbond_variants = [hbond, "-".join(hbond.split("-")[::-1])]
        cols_int = [f'combined_hbond_{i}' for i in range(1, 11)]  # safer

        for col in cols_int:
            if col in row:  # check if the column exists
                for hb in hbond_variants:
                    if isinstance(row[col], str) and row[col].startswith(hb):
                        return float(row[col].split('_')[1])
        return None
    
    suffix_groups = defaultdict(list)
    for col in df1.columns:
        suffix = '_'.join(col.split('_')[-2:])
    
        if suffix.startswith('hbond'):
            print (suffix)
            suffix_groups[suffix].append(col)
    
    # Combine values for each group with matching suffix
    for suffix, cols in suffix_groups.items():
        if len(cols) == 2:  # Only combine if exactly two columns share the suffix
            col1, col2 = cols
            new_col = f'combined_{suffix}'
            df1[new_col] = df1[col2].astype(str) + '_' + df1[col1].astype(str)
            
    for hbond in hbonds:
        df1[hbond] = df1.apply(lambda row: extract_bp(row, hbond), axis=1)
    
    df2= df1.dropna(subset= hbonds) #droping examples which do not contain all the hbonds user specified
    
    df3 = df2.drop(columns=[col for col in df.columns if col.startswith('combined')]) #removing the temp columns
    
    return df3

### Functions to extract meta data from RCSB

In [111]:
def get_info(p):
    en_dic={} #this dictionary will be populated for each entity id with chain list, molecule, organism, sequence, experiment, resolution information
    filename= p+'.cif'
    url= 'https://files.rcsb.org/view/%s' %filename #this url will extract experiment and resolution information 
    url_org = 'https://www.rcsb.org/structure/%s' %p #this url will extract experiment and resolution information
    url_seq= 'https://www.rcsb.org/fasta/entry/%s/display' %p #this url will extract information comes with fasta
    
    u = requests.get(url).content
    u_org = requests.get(url_org).content
    u_seq= requests.get(url_seq).content #fasta url for getting sequence information
    
    soup= BeautifulSoup(u_org, 'lxml')
    soup_seq= BeautifulSoup(u_seq, 'lxml')
    
    all_tables= pd.read_html(url_org) #in this list of tables, each tables contain detail information of each entity
    #however, we are using these tables only to extract chain ID and segment ID
    
    
    org= soup.find_all('li', id= 'header_organism') #html contents for source organism information
    se= soup_seq.find_all('body') #html contents for fasta

    #extracting experimental method information
    u1= str(u).split('#')
    for u2 in u1:  
        if '_exptl.method' in u2:
            exp_method=  u2.split("'")[1].replace('\\', '')
    
    #print (exp_method)
    #extracting resolution information 
    for u2 in u1:
        u3= u2.replace('_reconstruction.resolution_method', '')
        u4= u3.replace("'_refine.ls_d_res_high\\'", '')
        if '_em_3d_reconstruction.resolution' in u4:
            
            resolution1= (u4.replace('\\n', '').split('_em_3d_reconstruction.resolution')[1].split('_em_3d')[0]).replace(' ', '')
            if len(resolution1)==0:
                pass
            else:
                resolution= round(float(resolution1), 1)

        if '_refine.ls_d_res_high' in u4:
            print (u4)
            resolution1= (u4.replace('\\n', '').split('_refine.ls_d_res_high')[1].split('_refine.')[0]).replace(' ', '')
            if len(resolution1)==0:
                pass
            elif resolution1 =='.':
                pass
            else: 
                resolution= round(float(resolution1), 1)
            
         


    #getting detail information from fasta url
    for i in se:
        en_det=(str(i)[13: len(str(i))-11]).split('&gt;') #list of detail for each entity

    for i, j in enumerate(en_det):
        entity_id= (j.split('|')[0]).split('_')[1] #entity ID is a number, one for each entity.
        en_dic[entity_id]=[]
        #print (entity_id)
        
        for t1, t2 in enumerate(all_tables):
            if t2.shape== (1, 4): #protein entity table shape = (5, 6), nucleic acid entity table shape= (3, 6)
                pass
            else:
                #print (t2)
                if (type(t2.columns[0]))== tuple:
                    if t2.columns[0][0].split(':')[1][1:] == str(entity_id):
                        total_chain= (t2[t2.columns[1]][0])
        
        #extracting chain_list and seg_list
        chain_list=[]#list of chain ID for each entity ID, one entity can contain multiple chains
        #all the chain in one entity is same (not sure about this fact)
        seg_list=[] #list of seg ID for each entity ID, one entity can contain multiple segment
    
        
        #print (total_chain)
        #some examplex of total chain
        #PB [auth C0], VC [auth D0]
        #A, EB [auth FB]
        #A, C, E, G, IA, C, E, G, I, K, M, O Less --->example PDB: 4RMO
        
        #seg ID and chain ID can be interchanged in some fasta files 
        #therefore, seg ID and chain ID will be always extracted from the website
        total_chain_frags= total_chain.split(',')
        #print (total_chain_frags)
        for f1, f11 in enumerate(total_chain_frags): 
            f2= f11.replace('Less', '')
            #print (f2)
            if ']' in f2:
                list_str_total_chain= list(f2.split(']'))
                for h1, h2 in enumerate(list_str_total_chain):
                    list_str_total_chain[h1]= h2.replace(',', '')
                    list_str_total_chain[h1]= h2.replace(' ', '')
                if '' in list_str_total_chain:
                    list_str_total_chain.remove('')
                else:
                    pass
                
                for h1, h2 in enumerate(list_str_total_chain):
                    hh2= h2.split('[auth')
                    chain_list.append(hh2[1])
                    seg_list.append(hh2[0])
            else: 
                chain_list.append(f2.replace(' ', ''))
                seg_list.append(f2.replace(' ', ''))

        molecule= (j.split('|')[2]) #type of molecule
    
        organism= str(j.split('|')[3]).split('\n')[0] #this expressed organism
        if organism == 'null':
            organism = 'Not available'
        
        if len(org)==0:
            org_2= 'Not available'
        else:
            #find if multiple source organism is present
            org_1= (list(str(org[0]).split('>')))
            #print (org_1)
            org_2=''
            for or1, or2 in enumerate(org_1):
                if or2.endswith('</a'):
                    #print (or2)
                    org_2 += or2[:len(or2)-3]+ ', '
            org_2= org_2[: len(org_2)-2] #this is source organism
            #print (org_2)
    
        sequence= (j.split('|')[3]).split('\n')[1] #this the RNA sequence in expre
        #print (entity_id)
        #print (chain_list)
        #print (seg_list)
        
        en_dic[entity_id].append(chain_list) #chain list
        en_dic[entity_id].append(seg_list) #segment list
        en_dic[entity_id].append(molecule) #RNA type or protein type
        en_dic[entity_id].append(organism) #expressed organism
        en_dic[entity_id].append(org_2) #source organism
        en_dic[entity_id].append(sequence) #sequence
        en_dic[entity_id].append(exp_method) #experimental method
        en_dic[entity_id].append(resolution) #resolution
        #print (sequence)
    #print (en_dic)
    #en_dic[entity_id][0] --> chain list
    #en_dic[entity_id][1] --> segment list
    #en_dic[entity_id][2] --> molecule (eg. RNA type)
    #en_dic[entity_id][3] --> expressed organism
    #en_dic[entity_id][4] --> source organism
    #en_dic[entity_id][5] --> sequence
    #en_dic[entity_id][6] --> experimental method
    #en_dic[entity_id][7] --> resolution 
    
    return (en_dic)

In [112]:
#this function will extract meta data for unique IDs (PDB_ID+ chain_ID) in the col of df
#and return the data as a dictionary where 
#keys will be the unique IDs in the col column
#values will be meta data for the corresponding unique ID
def dict_pc_id(df, col):
    unq_pc_IDs= list(set(df[col].tolist()))

    print (unq_pc_IDs)
    D_pc_info={}
    for i, j in enumerate(unq_pc_IDs):
        print ('PROBLEM HERE')
        print (j)
        print ('======================> working with this unique ID' + j)
        p= j.split('_')[0] #PDB ID
        c= j.split('_')[1] #Chain ID
        D_PDB_all= get_info(p)
        for k in D_PDB_all: #k is the entity ID
            if c in D_PDB_all[k][0]:
                print (j)
                D_pc_info[j]= D_PDB_all[k]

    return D_pc_info

In [113]:
def populate_info(df):
    df['data_ext1'] = df['PDB_ID'].astype(str) + '_' + df['chain_ID_res1'].astype(str)
    df['data_ext2'] = df['PDB_ID'].astype(str) + '_' + df['chain_ID_res2'].astype(str)
    for m, n in enumerate(['data_ext1', 'data_ext2']):
        D_pc_info= dict_pc_id(df, n)
        for i, j in enumerate(df[n]):

            print ('==========================================')
            print (j)
            chain_ID= j.split('_')[1] #this is chain ID
            print (chain_ID)
            print (D_pc_info)
            list_chain_ID1= (D_pc_info[j][0])
            list_chain_ID=[]
            for ch1, ch2 in enumerate(list_chain_ID1):
                ch3= ch2.replace(' ', '')
                list_chain_ID.append(ch3)
            print ('WORKING HERE!!!')
            print (list_chain_ID)
            chain_ID_index= list_chain_ID.index(chain_ID) #this is chain ID index in the D_pc_info, to find the segment ID the same index can be used
        
            #df.loc[i, 'Experimental_Method']= D_pc_info[j][6]
            #df.loc[i, 'Resolution_(Å)']= D_pc_info[j][7]  
            df.loc[i, 'seg_ID_res'+str(m+1)]= D_pc_info[j][1][chain_ID_index]     
            df.loc[i, 'Molecule_res'+str(m+1)]= D_pc_info[j][2]
            #df.loc[i, 'Source_Organism']= D_pc_info[j][4]
            df.loc[i, 'Organism_res'+str(m+1)]= D_pc_info[j][3]
            df.loc[i, 'Chain_length_reference_res'+str(m+1)]= len(D_pc_info[j][5])

    return df


### Extracting/ calculating average temperature factors of atoms with or without backbone atoms included

In [114]:
#function to extract structure file in cif format and convert as a pandas dataframe
def extract_cif(p):
    filename= p+'.cif'
    url= 'https://files.rcsb.org/view/%s' %filename 
    u = requests.get(url).content
    u1= str(u).split('#')
    if len(u1)==1:
        print ('STRUCTURE IS NOT AVAILABLE!')
        return '0'
    
    else:
        c_intrst= ['_atom_site.group_PDB', '_atom_site.id', '_atom_site.type_symbol',
           '_atom_site.label_atom_id', '_atom_site.label_alt_id',
           '_atom_site.label_comp_id', '_atom_site.label_asym_id',
           '_atom_site.label_entity_id', '_atom_site.label_seq_id',
           '_atom_site.pdbx_PDB_ins_code', '_atom_site.Cartn_x',
           '_atom_site.Cartn_y', '_atom_site.Cartn_z', '_atom_site.occupancy',
           '_atom_site.B_iso_or_equiv', '_atom_site.pdbx_formal_charge',
           '_atom_site.auth_seq_id', '_atom_site.auth_comp_id',
           '_atom_site.auth_asym_id', '_atom_site.auth_atom_id',
           '_atom_site.pdbx_PDB_model_num', '###']
        u2=[]
        for i, j in enumerate(u1):
            if c_intrst[0] in j:
                u2.append(j)

        if len(u2)==2:
            if len(u2[0])> len(u2[1]):
                u3= u2[0].replace('      ', '$')
            else:
                u3= u2[1].replace('      ', '$')
        else:
            u3= u2[0].replace('      ', '$')
        u4= u3.replace('     ', '$')
        u5= u4.replace('    ', '$')
        u6= u5.replace('   ', '$')
        u7= u6.replace('  ', '$')
        u8= u7.replace(' ', '$')
        u9= u8.replace('$$', '$')
        u10= u9.replace('\\\\', '').split('\\n')
        
        if len(u10[24].split('$')) == 22:
            df = pd.DataFrame({'all_col':u10[23:]})
            df[c_intrst] = df['all_col'].str.split('$', expand=True)
            df= df.drop(['all_col', '###'], axis=1)
            
        elif len(u10[24].split('$')) == 23:
            c_intrst[21]= '_atom_site.calc_flag'
            c_intrst.append('###')
            df = pd.DataFrame({'all_col':u10[24:]})
            df[c_intrst] = df['all_col'].str.split('$', expand=True)
            df= df.drop(['all_col', '###'], axis=1)

        return df

In [115]:
#updated clip function (Feb 2025)
#this function will allow to clip residues from two (need to update so, any number of chain can be considered) different chain
def clip(p, r, h, F):
    #p= pdb_ID, entries can be case-insensitive
    #r= list of residues 
    #each residue information in the list above will be formatted like: chain_ID.residue_ID
    #h= 'N' or 'Y', if 'N', that means no hydrogen coordinates should be included considering hydrogen coordinates are provided 
    #if 'Y', that means no hydrogen coordinates should be removed if any hydrogen coordinates are provided
    #F= desired output filename (with the extension of '.cif' or '.pdb')
    P= p.upper()
    c_ids= list(set([i.split('.')[0] for i in r]))
    print (c_ids)

    p1= extract_cif(P)
    #print (p1)

    if len(p1)>1:
        p1['temp_col'] = p1[['_atom_site.auth_asym_id', '_atom_site.auth_seq_id', '_atom_site.pdbx_PDB_ins_code']].fillna("").agg('_'.join, axis=1).str.strip()
        p1['temp_col'] = p1['temp_col'].str.replace('?', '*', regex=True)
        # instead of filtering out by chain ID, segment ID, residue index, residue ID one after another
        # temp column will have chain ID, residue index, and insertion code all together
        # each row will have their unique items for this column
        print (p1['temp_col'])
        p2= p1[p1['temp_col'].isin(r)]
        p2.index= np.arange(0, len(p2))
        
        #print (p2.shape)

        #filtering out or not hydrogen atoms
        if h== 'N':
            p3= p2[p2['_atom_site.type_symbol']!= 'H']
            p3.index= np.arange(0, len(p3))
        else:
            p3= p2.copy()
        
        p3 = p3.drop(columns=['temp_col'])

        #cleaning name for the sugar atoms
        for i, j in enumerate(p3['_atom_site.label_atom_id']):
            if "\\'" in j:
                #print (j)
                #print (j)
                x= (j.replace("\\'", "'"))
                y= (x.replace('"', ''))
                p3.loc[i, '_atom_site.label_atom_id'] = y
                p3.loc[i, '_atom_site.auth_atom_id'] = y
        
        if F.split('.')[1]== 'pdb':
            #converting to pdb 
            columns_needed = ["_atom_site.id", "_atom_site.label_atom_id", "_atom_site.label_comp_id",
                          "_atom_site.auth_asym_id", "_atom_site.auth_seq_id", "_atom_site.pdbx_PDB_ins_code",
                          "_atom_site.Cartn_x", "_atom_site.Cartn_y", "_atom_site.Cartn_z",
                          "_atom_site.occupancy", "_atom_site.B_iso_or_equiv", "_atom_site.type_symbol"
                          ]
        
            # Ensure all required columns exist
            for col in columns_needed:
                if col not in p3.columns:
                    p3[col] = ""  # Fill missing columns with empty values

            # Open the output PDB file for writing
            with open(F, "w") as pdb_file:
                atom_serial_number = 1
                common_chain_ID= 'A' #temporary solution
                #main problem is what should be the solution if residues are from multiple chains?
                for _, row in p3.iterrows():
                    # Handle missing insertion codes (CIF uses '?' or '.' for no insertion code)
                    ins_code = row["_atom_site.pdbx_PDB_ins_code"]
                    ins_code = ins_code if ins_code not in ["?", "."] else " "
            
                    pdb_file.write(
                    f"ATOM  {atom_serial_number:>5}  {row['_atom_site.label_atom_id']:<4}"
                    f"{row['_atom_site.label_comp_id']:>3} {common_chain_ID}"
                    f"{int(row['_atom_site.label_seq_id']):>4}{ins_code:<1}   "
                    f"{float(row['_atom_site.Cartn_x']):>8.3f}{float(row['_atom_site.Cartn_y']):>8.3f}{float(row['_atom_site.Cartn_z']):>8.3f}"
                    f"{float(row['_atom_site.occupancy']):>6.2f}{float(row['_atom_site.B_iso_or_equiv']):>6.2f}          {row['_atom_site.type_symbol']:>2}\n")
                    atom_serial_number += 1
                
        else:
            #converting to cif
            #Creating dataframe for the column name
            c_intrst_1= ['_atom_site.group_PDB', '_atom_site.id', '_atom_site.type_symbol',
                '_atom_site.label_atom_id', '_atom_site.label_alt_id',
                '_atom_site.label_comp_id', '_atom_site.label_asym_id',
                '_atom_site.label_entity_id', '_atom_site.label_seq_id',
                '_atom_site.pdbx_PDB_ins_code', '_atom_site.Cartn_x',
                '_atom_site.Cartn_y', '_atom_site.Cartn_z', '_atom_site.occupancy',
                '_atom_site.B_iso_or_equiv', '_atom_site.pdbx_formal_charge',
                '_atom_site.auth_seq_id', '_atom_site.auth_comp_id',
                '_atom_site.auth_asym_id', '_atom_site.auth_atom_id',
                '_atom_site.pdbx_PDB_model_num']
            c_intrst_2= ['data_', '#','loop_', '_atom_site.group_PDB', '_atom_site.id', '_atom_site.type_symbol',
                '_atom_site.label_atom_id', '_atom_site.label_alt_id',
                '_atom_site.label_comp_id', '_atom_site.label_asym_id',
                '_atom_site.label_entity_id', '_atom_site.label_seq_id',
                '_atom_site.pdbx_PDB_ins_code', '_atom_site.Cartn_x',
                '_atom_site.Cartn_y', '_atom_site.Cartn_z', '_atom_site.occupancy',
                '_atom_site.B_iso_or_equiv', '_atom_site.pdbx_formal_charge',
                '_atom_site.auth_seq_id', '_atom_site.auth_comp_id',
                '_atom_site.auth_asym_id', '_atom_site.auth_atom_id',
                '_atom_site.pdbx_PDB_model_num']
    
            c_intrst_2[0]= 'data_'+P
    
            p4= pd.DataFrame(columns= c_intrst_1)
            p4['_atom_site.group_PDB']= c_intrst_2 #this p3 dataframe above p2 will be joined in p4. p3 will help pymol to visualize the file
    
            p5 = pd.concat([p4, p3], axis=0)

            print (p5.shape)

            #p5.to_csv(F, header= False, sep=' ', index= False) #comment out this line if you do not want to save the structure file
            
        return p3

In [116]:
def ext_tfactor(p, r, h, F, BB):
    #p= PDB_ID (in uppercase)
    
    #r= list of residues 
    #example list= ['A_N1_b', 'B_N2_*'']
    #first character (separated by '_') of each string is the chain_ID of the residue of interest
    #in the example above 'A' and 'B' are the chain ID
    #N1 and N2 are the residue index
    #the third character is the icode of the residue of interest
    #if there is no icode, then '*' will take place instead of the icode 
    
    #h= 'N' or 'Y', if 'N', that means no hydrogen coordinates should be included considering hydrogen coordinates are provided 
    #if 'Y', that means no hydrogen coordinates should be removed if any hydrogen coordinates are provided
    
    #F= desired output filename (with the extension of '.cif' or '.pdb')
    print ('===============================================')
    print (p)
    print (r)
    print (h)
    print (F)
    
    backbone_atoms= ["O5'",
                     "C5'",
                     "C4'",
                     "O4'",
                     "C3'",
                     "O3'",
                     "C2'",
                     "O2'",
                     "C1'",
                     'P',
                     'OP1',
                     'OP2']
    
    #cliping coordinates for the residue of interest from the complete structure 
    df= clip(p, r, h, 'nothing.cif')
    
    #remove backbone atoms
    if BB==0: #no backbone atoms should be included
        df1= df[~df['_atom_site.auth_atom_id'].isin(backbone_atoms)]
        df1.index= np.arange(0, len(df1))
    elif BB==1: #backbone atoms should be included
        df1= df.copy()
    
    #split res1 and res2
    df1['temp_col'] = df1[['_atom_site.auth_asym_id', '_atom_site.auth_seq_id', '_atom_site.pdbx_PDB_ins_code']].fillna("").agg('_'.join, axis=1).str.strip()
    df1['temp_col'] = df1['temp_col'].str.replace('?', '*', regex=True)
    
    df_res1= df1[df1['temp_col']==r[0]] #only res1 atoms will be stored here
    df_res1.index= np.arange(0, len(df_res1))
    
    df_res2= df1[df1['temp_col']==r[1]] #only res2 atoms will be stored here
    df_res2.index= np.arange(0, len(df_res2))
    
    #print ('we came this far ----------------------------------------------------------------------->>>>>')
    #print (df_res1['_atom_site.B_iso_or_equiv'])
    #print (df_res2['_atom_site.B_iso_or_equiv'])
    
    #calculate the average temp factor for res1 and res2
    b_res1= df_res1['_atom_site.B_iso_or_equiv'].astype(float).mean()
    b_res2= df_res2['_atom_site.B_iso_or_equiv'].astype(float).mean()
    
    print ('we came this far ----------------------------------------------------------------------->>>>>')
    print (b_res1)
    print (b_res2)
    
    return [b_res1, b_res2]

### Calculating coplanarity angles

In [117]:
def check_planarity(p, r, h, F):
    #p= PDB_ID (in uppercase)
    
    #r= list of residues 
    #example list= ['A_N1_b', 'B_N2_*'']
    #first character (separated by '_') of each string is the chain_ID of the residue of interest
    #in the example above 'A' and 'B' are the chain ID
    #N1 and N2 are the residue index
    #the third character is the icode of the residue of interest
    #if there is no icode, then '*' will take place instead of the icode 
    
    #h= 'N' or 'Y', if 'N', that means no hydrogen coordinates should be included considering hydrogen coordinates are provided 
    #if 'Y', that means no hydrogen coordinates should be removed if any hydrogen coordinates are provided
    
    #F= desired output filename (with the extension of '.cif' or '.pdb')
    print ('===============================================')
    print (p)
    print (r)
    print (h)
    print (F)
    atom_int= ['A_N9', 'A_C2', 'A_C6',
               'G_N9', 'G_C2', 'G_C6', 
               'C_N1', 'C_C2', 'C_C4',
               'U_N1', 'U_C2', 'U_C4']
    
    
    df= clip(p, r, h, 'nothing.cif')

    #df['temp_col'] = df[['_atom_site.auth_comp_id', '_atom_site.auth_atom_id']].fillna("").agg('_'.join, axis=1).str.strip()
    df['temp_col'] = (df[['_atom_site.auth_comp_id', '_atom_site.auth_atom_id']]
                    .fillna('')
                    .agg('_'.join, axis=1)
                    .str.strip()
                    )
    df['temp_col'] = df['temp_col'].str.replace(' ', '')
    print (df['temp_col'])
    
    
    #filtering out the atom of interest
    df1= df[df['temp_col'].isin(atom_int)]
    df1.index= np.arange(0, len(df1))
    
    df1 = df1.drop(columns=['temp_col'])
    
    coords1 = df1.iloc[0:3][['_atom_site.Cartn_x', '_atom_site.Cartn_y', '_atom_site.Cartn_z']].astype(float).values.tolist()
    coords2 = df1.iloc[3:6][['_atom_site.Cartn_x', '_atom_site.Cartn_y', '_atom_site.Cartn_z']].astype(float).values.tolist()
    
    

    print (df1)
    print (coords1)
    print (coords2)
    
    
    #import numpy as np

    def calculate_plane_normal(coords):
        """
        Calculate the normal vector of a plane defined by 3 atomic coordinates.
        :param coords: A (3, 3) numpy array where each row is [x, y, z] of one atom
        :return: A unit normal vector of the plane
        """
        v1 = coords[1] - coords[0]
        v2 = coords[2] - coords[0]
        normal = np.cross(v1, v2)
        return normal / np.linalg.norm(normal)

    def angle_between_planes(normal1, normal2):
        """
        Calculate the angle in degrees between two plane normal vectors.
        :param normal1: First normal vector (numpy array)
        :param normal2: Second normal vector (numpy array)
        :return: Angle in degrees
        """
        cos_theta = np.clip(np.dot(normal1, normal2), -1.0, 1.0)
        angle_rad = np.arccos(cos_theta)
        angle_deg = np.degrees(angle_rad)
        return min(angle_deg, 180 - angle_deg)

    def assess_coplanarity(coords1, coords2):
        """
        Assess the coplanarity of two RNA bases given 3 atoms from each.
        :param coords1: (3,3) array of atoms from residue 1
        :param coords2: (3,3) array of atoms from residue 2
        :return: Angle in degrees between the planes (0 = perfectly coplanar)
        """
        n1 = calculate_plane_normal(np.array(coords1))
        n2 = calculate_plane_normal(np.array(coords2))
        return angle_between_planes(n1, n2)
    
    angle= assess_coplanarity(coords1, coords2)
    
    print ('=========================')
    print (angle)
    return angle


# Data preparation

#### Step 1: importing list of base pair data from google drive

In [11]:
#import data as csv

#importing option 1: from local directory
#df_bp= pd.read_csv('/Users/jonesyy/Downloads/SROP Work/data/06_06_25/all_bps_with_all_regs_apr_2025.csv')


#importing option 2: importing using the Google drive link 
# #the google drive link should give editor access 
url = 'https://drive.google.com/file/d/1sL2JUIHRMAOFo7k8mjKveVF2RGcu7q-4/view?usp=drive_link' #X-Ray_Cryo-em
#url= 'https://drive.google.com/file/d/1I5GsOlCdIdY3iTc6wFQoTdsMWKj64vHA/view?usp=drive_link' #NMR

# Convert to a downloadable link
file_id = url.split('/d/')[1].split('/')[0]
download_url = f'https://drive.google.com/uc?id={file_id}'

# Download the file
output = 'data.csv'
gdown.download(download_url, output, quiet=False)

# Load into pandas
df_bp = pd.read_csv(output)

# Delete the downloaded CSV file
os.remove(output)

Downloading...
From (original): https://drive.google.com/uc?id=1sL2JUIHRMAOFo7k8mjKveVF2RGcu7q-4
From (redirected): https://drive.google.com/uc?id=1sL2JUIHRMAOFo7k8mjKveVF2RGcu7q-4&confirm=t&uuid=e97d6634-4b5d-431f-b906-7bff8ed1c991
To: /Users/jonesyy/Documents/GitHub/identify_Homo_base_pairs/scripts/data.csv
100%|██████████| 739M/739M [00:20<00:00, 36.8MB/s] 
/var/folders/t1/d9jqqs655cs0r3yvpzy6s6280000gn/T/ipykernel_7225/492745326.py:21: DtypeWarning: Columns (4,9,33,34,35,36,39,41) have mixed types. Specify dtype option on import or set low_memory=False.
  df_bp = pd.read_csv(output)


#### Step 2: Fixing '5E54' becoming '5.00E+54' issue

In [12]:
df_bp1= fix_PDB_ID(df_bp)

157D
157D
157D
157D
157D
157D
157D
157D
157D
157D
157D
157D
165D
165D
165D
165D
165D
165D
165D
165D
1A34
1A34
1A34
1A34
1A34
1A34
1A34
1A34
1A34
1A9N
1A9N
1A9N
1A9N
1A9N
1A9N
1A9N
1A9N
1A9N
1A9N
1A9N
1A9N
1AQ3
1AQ3
1AQ3
1AQ3
1AQ3
1AQ3
1AQ3
1AQ3
1AQ4
1AQ4
1AQ4
1AQ4
1AQ4
1AQ4
1AQ4
1AQ4
1AQ4
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASY
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1ASZ
1B23
1B23
1B23


KeyboardInterrupt: 

#### Step 3: Dropping null residue indexes 

In [15]:
df_bp2 = df_bp.dropna(subset=['res_index_res1', 'res_index_res2'])
df_bp2.index= np.arange(0, len(df_bp2))

#### Step 4: Making sure icode columns will not contain null values

In [16]:
#making sure icode columns will not contain null values
df_bp2['icode_res1'] = df_bp2['icode_res1'].fillna('*')
df_bp2['icode_res1'] = df_bp2['icode_res1'].replace('nan', '*')

df_bp2['icode_res2'] = df_bp2['icode_res2'].fillna('*')
df_bp2['icode_res2'] = df_bp2['icode_res2'].replace('nan', '*')


#converting residue index into integer
df_bp2['res_index_res1'] = df_bp2['res_index_res1'].astype(float).astype(int).astype(str)
df_bp2['res_index_res2'] = df_bp2['res_index_res2'].astype(float).astype(int).astype(str)

/var/folders/t1/d9jqqs655cs0r3yvpzy6s6280000gn/T/ipykernel_7225/703794337.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_bp2['icode_res1'] = df_bp2['icode_res1'].fillna('*')
/var/folders/t1/d9jqqs655cs0r3yvpzy6s6280000gn/T/ipykernel_7225/703794337.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_bp2['icode_res1'] = df_bp2['icode_res1'].replace('nan', '*')
/var/folders/t1/d9jqqs655cs0r3yvpzy6s6280000gn/T/ipykernel_7225/703794337.py:5: SettingWithCopyWarning: 
A value is trying to be set on a co

#### Step 5: Removing any hydrogen bonds which can result into some weird unstable base pairs

In [17]:
df_bp2 = df_bp2[~df_bp2['atoms_ID_hbond_1'].str.contains("'", regex=False, na=False)]
df_bp2.index= np.arange(0, len(df_bp2))

df_bp2 = df_bp2[~df_bp2['atoms_ID_hbond_2'].str.contains("'", regex=False, na=False)]
df_bp2.index= np.arange(0, len(df_bp2))

df_bp2 = df_bp2[~df_bp2['atoms_ID_hbond_3'].str.contains("'", regex=False, na=False)]
df_bp2.index= np.arange(0, len(df_bp2))

df_bp2 = df_bp2[~df_bp2['atoms_ID_hbond_1'].str.contains("OP", regex=False, na=False)]
df_bp2.index= np.arange(0, len(df_bp2))

df_bp2 = df_bp2[~df_bp2['atoms_ID_hbond_2'].str.contains("OP", regex=False, na=False)]
df_bp2.index= np.arange(0, len(df_bp2))

df_bp2 = df_bp2[~df_bp2['atoms_ID_hbond_3'].str.contains("OP", regex=False, na=False)]
df_bp2.index= np.arange(0, len(df_bp2))

#### Step 6: (optional) Removing any base pair involved with DNA or covalently modified residues

In [18]:
df_bp2['bp_name_res']= df_bp2['res_ID_res1']+'-'+df_bp2['res_ID_res2']
df_bp3= df_bp2[(df_bp2['bp_name_res']== df_bp2['base_pair'])]
df_bp3.index= np.arange(0, len(df_bp3))

In [19]:
print (df_bp2.shape)
print (df_bp3.shape)

(3180686, 50)
(2792231, 50)


#### Step 7: Replacing '--' from the name column to 'undefined' 

In [20]:
df_bp3['name'] = df_bp3['name'].replace('--', 'undefined')
df_bp3['name'] = df_bp3['name'].replace('WC', 'WCF')

/var/folders/t1/d9jqqs655cs0r3yvpzy6s6280000gn/T/ipykernel_7225/1685092079.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_bp3['name'] = df_bp3['name'].replace('--', 'undefined')
/var/folders/t1/d9jqqs655cs0r3yvpzy6s6280000gn/T/ipykernel_7225/1685092079.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_bp3['name'] = df_bp3['name'].replace('WC', 'WCF')


#### Step 8: Droping atom serial number columns 

In [21]:
columns_to_drop=[]
for cols in df_bp3.columns:
    if cols.startswith('atoms_serNum'):
        columns_to_drop.append(cols)
    
df_bp4 = df_bp3.drop(columns=columns_to_drop).copy()

In [22]:
df_bp4.shape

(2792231, 40)

#### Step 9: Applying a distance cut-off for all hbonds 

In [23]:
dcols=[]
for cols in df_bp4.columns:
    if cols.startswith('distance'):
        dcols.append(cols)
df_bp4[dcols] = df_bp4[dcols].astype(float)
df_bp5 = df_bp4[~((df_bp4[dcols] > 3.4).any(axis=1))]
df_bp5[dcols] = df_bp5[dcols].astype(str)
df_bp5.index= np.arange(0, len(df_bp5))

/var/folders/t1/d9jqqs655cs0r3yvpzy6s6280000gn/T/ipykernel_7225/3081988079.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_bp5[dcols] = df_bp5[dcols].astype(str)


#### Step 10: Applying a resolution cut-off 

In [24]:
df_bp5['Resolution_(Å)'] = df_bp5['Resolution_(Å)'].astype(float)
df_bp6 = df_bp5[~(df_bp5['Resolution_(Å)'] > 3)]
df_bp6.index= np.arange(0, len(df_bp6))


/var/folders/t1/d9jqqs655cs0r3yvpzy6s6280000gn/T/ipykernel_7225/1441594956.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_bp5['Resolution_(Å)'] = df_bp5['Resolution_(Å)'].astype(float)


In [3]:
df_bp.columns

Index(['PDB_ID', 'Experimental_Method', 'Resolution_(Å)', 'nt1',
       'chain_ID_res1', 'res_ID_res1', 'res_index_res1', 'icode_res1', 'nt2',
       'chain_ID_res2', 'res_ID_res2', 'res_index_res2', 'icode_res2',
       'base_pair', 'name', 'Saenger', 'LW', 'DSSR', 'bp_res',
       'distance_hbond_1', 'distance_hbond_2', 'distance_hbond_3',
       'atoms_serNum_hbond_1', 'atoms_serNum_hbond_2', 'atoms_serNum_hbond_3',
       'atoms_ID_hbond_1', 'atoms_ID_hbond_2', 'atoms_ID_hbond_3',
       'distance_hbond_4', 'atoms_serNum_hbond_4', 'atoms_ID_hbond_4',
       'distance_hbond_5', 'distance_hbond_6', 'atoms_serNum_hbond_5',
       'atoms_serNum_hbond_6', 'atoms_ID_hbond_5', 'atoms_ID_hbond_6',
       'distance_hbond_7', 'distance_hbond_8', 'atoms_serNum_hbond_7',
       'atoms_serNum_hbond_8', 'atoms_ID_hbond_7', 'atoms_ID_hbond_8',
       'distance_hbond_9', 'atoms_serNum_hbond_9', 'atoms_ID_hbond_9',
       'distance_hbond_10', 'atoms_serNum_hbond_10', 'atoms_ID_hbond_10'],
      dty

In [21]:
df_bp.shape

(3728509, 49)

In [25]:
df_bp6

PDB_ID Experimental_Method  Resolution_(Å)    nt1 chain_ID_res1  \
0         157D   X-RAY DIFFRACTION             1.8   A.A5             A   
1         157D   X-RAY DIFFRACTION             1.8   A.A6             A   
2         157D   X-RAY DIFFRACTION             1.8   A.A9             A   
3         157D   X-RAY DIFFRACTION             1.8   A.C1             A   
4         157D   X-RAY DIFFRACTION             1.8  A.C11             A   
...        ...                 ...             ...    ...           ...   
1403980   9QRP   X-RAY DIFFRACTION             2.7  T.G69             T   
1403981   9QRP   X-RAY DIFFRACTION             2.7   T.G7             T   
1403982   9QRP   X-RAY DIFFRACTION             2.7  T.G70             T   
1403983   9QRP   X-RAY DIFFRACTION             2.7  T.G71             T   
1403984   9QRP   X-RAY DIFFRACTION             2.7   T.G9             T   

        res_ID_res1 res_index_res1 icode_res1    nt2 chain_ID_res2  ...  \
0                 A              5          *  B.U20             B  ...   
1                 A              6          *  B.U19             B  ...   
2                 A              9          *  B.G16             B  ...   
3                 C              1          *  B.G24             B  ...   
4                 C             11          *  B.G14             B  ...   
...             ...            ...        ...    ...           ...  ...   
1403980           G             69          *  T.C81             T  ...   
1403981           G              7          *  T.C84             T  ...   
1403982           G             70          *  T.C80             T  ...   
1403983           G             71          *  T.C79             T  ...   
1403984           G              9          *  T.A14             T  ...   

        atoms_ID_hbond_6 distance_hbond_7 distance_hbond_8 atoms_ID_hbond_7  \
0                    NaN              nan              nan              NaN   
1                    NaN              nan              nan              NaN   
2                    NaN              nan              nan              NaN   
3                    NaN              nan              nan              NaN   
4                    NaN              nan              nan              NaN   
...                  ...              ...              ...              ...   
1403980              NaN              nan              nan              NaN   
1403981              NaN              nan              nan              NaN   
1403982              NaN              nan              nan              NaN   
1403983              NaN              nan              nan              NaN   
1403984              NaN              nan              nan              NaN   

        atoms_ID_hbond_8 distance_hbond_9 atoms_ID_hbond_9 distance_hbond_10  \
0                    NaN              nan              NaN               nan   
1                    NaN              nan              NaN               nan   
2                    NaN              nan              NaN               nan   
3                    NaN              nan              NaN               nan   
4                    NaN              nan              NaN               nan   
...                  ...              ...              ...               ...   
1403980              NaN              nan              NaN               nan   
1403981              NaN              nan              NaN               nan   
1403982              NaN              nan              NaN               nan   
1403983              NaN              nan              NaN               nan   
1403984              NaN              nan              NaN               nan   

        atoms_ID_hbond_10 bp_name_res  
0                     NaN         A-U  
1                     NaN         A-U  
2                     NaN         A-G  
3                     NaN         C-G  
4                     NaN         C-G  
...                   ...         ...  
1403980         

In [26]:
df_bp6['name'].value_counts()

name
WCF            999782
undefined      162693
Wobble         126864
rHoogsteen      45927
Sheared         19283
Imino           18158
~rHoogsteen     12286
~Wobble          7783
~Sheared         6158
Platform         2715
Calcutta         2181
Metal             155
Name: count, dtype: int64

In [39]:
df_bp6.shape

 

(1403985, 40)

# Identifying base pair of interest

In [29]:
#AC_r2= find_bp_interest(df_bp6, 'A-C', ['A.N6-C.N4', 'A.N1-C.N3'])
#GG_ad= find_bp_interest(df_bp5, 'G-G', ['G.N6-G.N6', 'G.N1-G.N1', 'G.N2-G.N2'])
AA_ad= find_bp_interest(df_bp6, 'A-A', ['A.N6-A.N6', 'A.N1-A.N1'])

hbond_1
hbond_2
hbond_3
hbond_1
hbond_2
hbond_3
hbond_4
hbond_4
hbond_5
hbond_6
hbond_5
hbond_6
hbond_7
hbond_8
hbond_7
hbond_8
hbond_9
hbond_9
hbond_10
hbond_10


/var/folders/t1/d9jqqs655cs0r3yvpzy6s6280000gn/T/ipykernel_7225/2864412857.py:34: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df1[new_col] = df1[col2].astype(str) + '_' + df1[col1].astype(str)
/var/folders/t1/d9jqqs655cs0r3yvpzy6s6280000gn/T/ipykernel_7225/2864412857.py:34: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df1[new_col] = df1[col2].astype(str) + '_' + df1[col1].astype(str)
/var/folders/t1/d9jqqs655cs0r3yvpzy6s6280000gn/T/ipykernel_7225/2864412857.py:34: SettingWithCopyWarning: 
A value is tryi

In [30]:
AA_ad

PDB_ID  Experimental_Method  Resolution_(Å)        nt1 chain_ID_res1  \
916     3JCS  ELECTRON MICROSCOPY           2.800     2.A607             2   
968     3VJR    X-RAY DIFFRACTION           2.400      B.A33             B   
1024    4K50    X-RAY DIFFRACTION           2.930     J.A581             J   
1505    4U4R    X-RAY DIFFRACTION           2.801     2.A477             2   
3658    5J5B    X-RAY DIFFRACTION           2.800   DA.A2117            DA   
3704    5J7L    X-RAY DIFFRACTION           3.000   DA.A2117            DA   
3776    5J91    X-RAY DIFFRACTION           2.960   DA.A2117            DA   
4548    6ID0  ELECTRON MICROSCOPY           2.900      F.A41             F   
5050    6T4Q  ELECTRON MICROSCOPY           2.600      7.A26             7   
5234    6V3A  ELECTRON MICROSCOPY           2.820  sN1.A1405           sN1   
5836    6YDP  ELECTRON MICROSCOPY           3.000     AV.A23            AV   
6963    7N2U  ELECTRON MICROSCOPY           2.530   23.A2117            23   
7500    7OSA    X-RAY DIFFRACTION           3.000  25S.A2462           25S   
7600    7OYD  ELECTRON MICROSCOPY           2.300    5.A2408             5   
7970    7QH7  ELECTRON MICROSCOPY           2.890    A.A1844             A   
8455    7RYH  ELECTRON MICROSCOPY           2.430     a.A452             a   
9044    7UVX  ELECTRON MICROSCOPY           2.350     a.A452             a   
9060    7UVY  ELECTRON MICROSCOPY           2.390     a.A452             a   
9093    7UW1  ELECTRON MICROSCOPY           2.210     a.A452             a   
9702    8ANY  ELECTRON MICROSCOPY           2.850     Ay.A26            Ay   
10347   8CRE    X-RAY DIFFRACTION           3.000     1.A988             1   
12284   8IP8  ELECTRON MICROSCOPY           2.900    aa.A143            aa   
13153   8QOI  ELECTRON MICROSCOPY           1.900    S2.A529            S2   
14362   8WHX  ELECTRON MICROSCOPY           2.800    A.A2340             A   
14730   8ZHC  ELECTRON MICROSCOPY           2.300    S2.A892            S2   
14803   9AX8  ELECTRON MICROSCOPY           2.600     A.A849             A   
14845   9AXU  ELECTRON MICROSCOPY           1.940    2.A1654             2   
14983   9B0G  ELECTRON MICROSCOPY           2.570    S2.A529            S2   
14996   9B0H  ELECTRON MICROSCOPY           2.590    S2.A529            S2   
15033   9B0O  ELECTRON MICROSCOPY           2.830    S2.A529            S2   
15057   9B0R  ELECTRON MICROSCOPY           2.810    S2.A529            S2   
15083   9B11  ELECTRON MICROSCOPY           2.770    S2.A529            S2   
16644   9MQT  ELECTRON MICROSCOPY           2.430     A.A262             A   
16646   9MQU  ELECTRON MICROSCOPY           2.590     A.A262             A   
16693   9NL5  ELECTRON MICROSCOPY           3.000   R1.A2117            R1   

      res_ID_res1 res_index_res1 icode_res1        nt2 chain_ID_res2  ...  \
916             A            607          *     2.A623             2  ...   
968             A             33          *      D.A33             D  ...   
1024            A            581          *     J.A598             J  ...   
1505            A            477          *     2.A511             2  ...   
3658            A           2117          *   DA.A2171            DA  ...   
3704            A           2117          *   DA.A2171            DA  ...   
3776            A           2117          *   DA.A2171            DA  ...   
4548            A             41          *       G.A6             G  ...   
5050            A             26          *      7.A44             7  ...   
5234            A           1405          *  sN1.A1489           sN1  ...   
5836            A             23          *     AV.A41            AV  ...   
6963            A           2117          *   23.A2170            23  ...   
7500            A           2462          *  25S.A2494           25S  ...   
7600            A           2408          *    5.A2791             5  ...   
7970            A           1844          

In [41]:
small_test= df_bp6.sample(n=3, random_state=7)
small_test.index= np.arange(0,len(small_test))

In [42]:
small_test

PDB_ID  Experimental_Method  Resolution_(Å)      nt1 chain_ID_res1  \
0   8ZGR  ELECTRON MICROSCOPY            2.70  S2.G514            S2   
1   8G5Z  ELECTRON MICROSCOPY            2.64    At.C2            At   
2   7S1I  ELECTRON MICROSCOPY            2.48   C.G138             C   

  res_ID_res1 res_index_res1 icode_res1      nt2 chain_ID_res2  ...  \
0           G            514          *  S2.C543            S2  ...   
1           C              2          *   At.G71            At  ...   
2           G            138          *   C.C225             C  ...   

  atoms_ID_hbond_6 distance_hbond_7 distance_hbond_8 atoms_ID_hbond_7  \
0              NaN              nan              nan              NaN   
1              NaN              nan              nan              NaN   
2              NaN              nan              nan              NaN   

  atoms_ID_hbond_8 distance_hbond_9 atoms_ID_hbond_9 distance_hbond_10  \
0              NaN              nan              NaN               nan   
1              NaN              nan              NaN               nan   
2              NaN              nan              NaN               nan   

  atoms_ID_hbond_10 bp_name_res  
0               NaN         G-C  
1               NaN         C-G  
2               NaN         G-C  

[3 rows x 40 columns]

In [43]:
#populate data from RCSB
df_bp6= populate_info(df_bp6) #replace df with the df for which you want to extract the information from RCSB


/var/folders/t1/d9jqqs655cs0r3yvpzy6s6280000gn/T/ipykernel_7225/2506774844.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['data_ext1'] = df['PDB_ID'].astype(str) + '_' + df['chain_ID_res1'].astype(str)
/var/folders/t1/d9jqqs655cs0r3yvpzy6s6280000gn/T/ipykernel_7225/2506774844.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['data_ext2'] = df['PDB_ID'].astype(str) + '_' + df['chain_ID_res2'].astype(str)


['9AZS_S2', '7Q0R_A', '8HTZ_A', '2NZ4_H', '7Q08_1', '8B0X_X', '6AZ3_6', '9DRV_F', '8GWB_I', '9B00_1v', '6CU1_A', '5NOM_A', '8YUO_V', '7UG7_16', '8BGH_2', '7SFR_a', '7U2H_1A', '9IWG_A', '8G2A_1a', '1KUQ_B', '2NUG_C', '4V99_Fc', '8I0V_H', '7PLI_D', '7M2T_ZZ', '8E48_I', '4V88_A3', '8V83_6', '7QCA_S60', '9BUP_AB', '8B2L_A3', '4X4T_B', '6WOO_2', '9JM0_N', '1RLG_C', '6Y2L_L5', '7QVP_A5', '8UD8_2A', '7NWT_2', '1NUV_C', '7JJU_A', '6BMD_A', '8AGV_y', '6E8S_A', '4V8G_BB', '8JDJ_E', '8CGU_a', '9IWF_A', '9E6Q_2', '4U24_DA', '3DH3_F', '9L6X_D', '7U2H_1B', '1H3E_B', '8EKB_2v', '3OV7_C', '8Y0B_B', '6OF1_2x', '9IOA_F', '7ASM_B', '8C01_2', '6WY3_C', '3EPH_E', '8PV3_C3', '5FJ1_D', '9D7S_1y', '8FZH_B', '8B2L_C3', '3BNO_A', '9G30_3', '8HFR_2f', '5IBB_1L', '7WI9_V', '4YVJ_C', '8E49_J', '8T6Y_B', '7N1P_mR', '8Y9N_B', '7EDU_C', '8G6Y_b', '3OL6_J', '6ZMI_S2', '7MT2_y', '9B0G_L8', '7ECM_A', '9DFE_2A', '9GMX_T', '7ZAH_5', '8AGW_y', '6YW5_aa', '2BS1_R', '8RQ0_A', '4W2H_CA', '4V9H_AV', '5UEE_A', '4W5T_B', '5WIT_1

FeatureNotFound: Couldn't find a tree builder with the features you requested: lxml. Do you need to install a parser library?

In [ ]:
#extract and populate temperature factors
#replace df with the dataframe of interest
#update the 'col1' and 'col2' with the columns where you want to store the temperature factors
#the last input for the function below is '1' if you want to include backbone atoms, otherwise use '0' to exclude backbone atoms
df[['col1', 'col2']] = df.apply(lambda row: pd.Series(ext_tfactor(row['PDB_ID'], 
                                                                [f"{row['chain_ID_res1']}_{row['res_index_res1']}_{row['icode_res1']}",
                                                                f"{row['chain_ID_res2']}_{row['res_index_res2']}_{row['icode_res2']}"],
                                                                'N',
                                                                'nothing.cif',
                                                                1)), axis=1)

In [ ]:
#extract/ calculate the planarity of the base pair
df['angle_univec'] = df.apply(lambda row: check_planarity(row['PDB_ID'], 
                                                                [f"{row['chain_ID_res1']}_{row['res_index_res1']}_{row['icode_res1']}",
                                                                f"{row['chain_ID_res2']}_{row['res_index_res2']}_{row['icode_res2']}"],
                                                                'N',
                                                                'nothing.cif'
                                                               ), axis=1)